<H1> Lab 2 -- Calculating Transport </H1>

<H2> Load Packages </H2>

Hit shift-enter on the following lines

In [ ]:
%pylab inline

In [ ]:
import kwant

In [ ]:
from scipy.sparse import * # Loads in the sparse array data structure

In [ ]:
import scipy.sparse.linalg as sl

In [ ]:
import scipy.linalg as lin

In [ ]:
# This is a long cell -- don't bother reading, just hit shift-enter
import IPython.display as d
from pylab import real,imag,array,log10
def mattohtml(ar1,tol=10**-5):
    """mat to html generates html code to display a matrix ar.  It works on matrices of both real and complex
    numbers.  If you have a sparse array, you need to convert it into dense form first.  It takes a second
    optional argument -- "tol".  Any entries smaller than tol are truncated"""
    ar=array(ar1) # convert to array
    # The html string will be stored as st
    st="""<div style="max-width:1000px;max-height:400px;border:1px solid #ccc;font:9px/11px  Courier, monospace;overflow:auto;"><table>"""
    for row in ar:
        st+="<tr>" # add new row in html table
        for element in row:
            st+="""<td style="border:1px solid #ccc">""" # add new element to html table
            st+=numform(element,tol) # add number to table
            st+="</td>"
        st+="</tr>"
    st+="</table>"
    return st
def numform(element,tol):
            """numform returns a string representing num -- the string is blank if |num|<tol"""
            st=""
            reelement=real(element)
            imelement=imag(element)
            if abs(reelement)<tol: # don't print the real part
                if abs(imelement)>tol: # print the imag part
                    st+=inumform(imelement)
                    st+="i"
            elif abs(imag(element))<tol: # print real but not imag
                st+=rnumform(reelement)
            else:                       # print both
                st+=rnumform(reelement)
                if imelement>0:
                    st+="+"
                else:
                    st+="-"
                    imelement=-imelement
                st+=inumform(imelement)
                st+="i"
            return st
def inumform(num):
    st=""
    if abs(num)<999 and abs(num)>0.01:
        if round(100*num)%100==0:
            st+="%.0f"%num
        elif round(100*num)%10==0:
            st+="%.1f"%num
        else:
            st+="%.2f"%num
    else:
        exp=int(log10(abs(num)))
        mant=int(10*(num/10**exp))/10.
        st+="("
        st+="$%.1f"%mant
        st+=r"\cdot10^{"
        st+=str(exp)
        st+=r"}$"
        st+=")"
        #st+="(%.1e)"%num
    return st
def rnumform(num):
    st=""
    if abs(num)<999 and abs(num)>0.01:
        if round(100*num)%100==0:
            st+="%.0f"%num
        elif round(100*num)%10==0:
            st+="%.1f"%num
        else:
            st+="%.2f"%num
    else:
        exp=int(log10(abs(num)))
        mant=int(10*(num/10**exp))/10.
        st+="$%.1f"%mant
        st+=r"\cdot10^{"
        st+=str(exp)
        st+=r"}$"
        #st+="%.1e"%num
    return st
def showmat(ar,tol=10**-5):
    try:
        ar=ar.todense()
    except:
        pass
    return d.HTML(mattohtml(array(ar),tol))

<H2> Problem 1: Calculating Greens Functions </H2>

Here is some sample code to generate a Greens function for a simple chain of length 10

In [ ]:
tstham=dia_matrix(((-ones(10),-ones(10)),(-1,1)),shape=(10,10)) # Make Matrix
showmat(tstham)                                                 # Show

here is how to make an identity matrix

In [ ]:
showmat(eye(10))

For a fixed energy $\omega$, we want $G=1/(\omega {\bf \cal I}-{\bf H})$, where $\bf \cal I$ is the identity matrix.  Since we want to do this for different $\omega$, we make this a function

In [ ]:
def tstgreen(omega):
    size=tstham.shape[0] # How big is the hamiltonian -- we could have hard-coded, but this is better
    invg=omega*eye(size)-tstham.todense() #
    return lin.inv(invg)

With this Greens function we can generate a local density of states as follows:

In [ ]:
ldosgrid=[]
for w in arange(-4,4,0.02):
    green=tstgreen(w-0.04j)
    ldos=2*imag(green.diagonal())
    ldosgrid.append(ldos)

In [ ]:
imshow(ldosgrid,extent=[0,9,-4,4])
xlabel("site")
ylabel("energy")
colorbar()

Clearly we can see 10 different energies where we have spectral weight -- and we can see the spatial distribution of the various modes.

It is interesting to compare the density of states at the center of the wire, and at the edge.  I will add more broadening to make it clearer.

In [ ]:
wvals=[]
centerdos=[]
edgedos=[]
for w in arange(-4,4,0.02):
    green=tstgreen(w-0.4j)
    ldos=2*imag(green.diagonal())
    wvals.append(w)
    centerdos.append(ldos[5])
    edgedos.append(ldos[0])

In [ ]:
plot(wvals,centerdos,wvals,edgedos)

Find the density of states at the center and edge of a wire for a wire of length 100.  [Use an appropriate broadening -- the one I used is too big for the longer wire.]  Compare to the exact results from class.  Feel free to change the above code -- or you can copy it below and make the changes.

<H2>Problem 2: Greens functions and self-energies from Kwant</H2>

Kwant is a quantum transport package described in: <a href="https://downloads.kwant-project.org/doc/kwant-paper.pdf">Kwant: a software package for quantum transport</a>.  It has some nice tools for constructing tight-binding Hamiltonians for arbitrarily shaped devices, and has tools for analyzing leads attached to these devices.  It actually does things a bit differently from what we did in class:  Rather than working with Greens functions, it works with wave-functions.  These are equivalent -- and we can always construct the Greens function from the spectral representation.

The documentation for kwant can be found at: <a href="https://kwant-project.org/doc/"> docs</a>, and a nice tutorial on quantum transport using kwant is at: <a href="https://kwant-project.org/mm16">March Meeting tutorial</a>.  Finally, I ran accross some class notes at: <a href="https://wiki.physics.udel.edu/phys824/Computer_Lab#Quantum_transport_simulations_using_KWANT_package">Branislav K. Nikolic, Introduction to Nanophysics</a>.  All of these have great examples of interesting transport problems one can explore with these tools.  There is also an interesting MOOC at <a href="https://topocondmat.org">MOOC</a>.

Here we are going to use these tools to explore the basic system we played with in class:  a 1D wire, where we consider a single  site to be our device, and the rest to be leads

For our example, all sites will lie upon a regular 1D lattice.  The first thing we do is tell the computer about this.

In [ ]:
chain_geometry=kwant.lattice.chain() # defines a 1D chain -- with lattice constant 1 -- knows things like what the neightbors are

Next we create a blank container, that we will fill with all of the information about our device.  It is kind of like making a matrix of zeros, that we will then fill in the matrix elements of.

In [ ]:
device=kwant.Builder() # the representation of our device

In [ ]:
device[chain_geometry(0)]=0 # add a single site to the device -- with an on-site energy of 0

Now all we need to do is to make the leads.  The leads are periodic -- to tell the computer about this symmetry we use

In [ ]:
xsym=kwant.TranslationalSymmetry((1,)) # defines a translational symmetry in the x direction
negxsym=kwant.TranslationalSymmetry((-1,))

We then can build the right lead.  We use the same container object (called kwant.Builder) that we used for the device.  But this time we tell it about the symmetry

In [ ]:
rightlead=kwant.Builder(xsym)
rightlead[chain_geometry(1)]=0 # Adds one site to lead -- because of symmetry, this actually adds an infinite number
rightlead[(chain_geometry(1),chain_geometry(2))]=-1 # adds one hopping element to lead -- again, because of symmetry this adds all the hoppings

Next the left lead

In [ ]:
leftlead=kwant.Builder(negxsym)
leftlead[chain_geometry(-1)]=0 # Adds sites to lead
leftlead[(chain_geometry(-1),chain_geometry(-2))]=-1 # adds hopping to lead

Here is the syntax for attaching the leads

In [ ]:
device.attach_lead(rightlead)
device.attach_lead(leftlead)

We can then get a visual representation of the device.  Leads are in red, while the device is in black

In [ ]:
kwant.plot(device,num_lead_cells=10);

So far, everything has been very high-level:  We have just specified geometry.  We now tell the computer to actually calculate the matrix H, the self-energies, etc.

In [ ]:
finaldevice=device.finalized() # This creates an object which knows all the technical bits

For example, we can extract the $1\times1$ matrix Hamiltonian

In [ ]:
h=finaldevice.hamiltonian_submatrix()
h

We can also get what the Hamiltonian is that represents 2 unit cells of one of the leads.

In [ ]:
finaldevice.leads[0].hamiltonian_submatrix()

or better yet, separately extract $H$ and $\Lambda$

In [ ]:
finaldevice.leads[0].cell_hamiltonian()

In [ ]:
finaldevice.leads[0].inter_cell_hopping()

We can extract the self-energies.  These are numerical functions of energy.

In [ ]:
rightleadselfenergy=finaldevice.leads[0].selfenergy
leftleadselfenergy=finaldevice.leads[0].selfenergy

We can compare these to the expression we found in lecture -- the following gets all of the branch cuts right if we add an infinitesmal positive imaginary to the energy.

In [ ]:
def theoryselfenergy(e):
    return e/2-1j*sqrt(1-e**2/4)

In [ ]:
elist=arange(-3.0,3,0.1)
rslist=[rightleadselfenergy(e)[0,0] for e in elist]
tslist=array([theoryselfenergy(e+0.00001j) for e in elist])

In [ ]:
plot(elist,real(rslist))
plot(elist,real(tslist),".")

In [ ]:
plot(elist,imag(rslist))
plot(elist,imag(tslist),".")

We can also extract the density of states

In [ ]:
filtelist=elist[abs(abs(elist)-2)>1e-3] # get rid of energy points too close to singularities

In [ ]:
dos=[kwant.ldos(finaldevice,e) for e in filtelist]

In [ ]:
def theorydos(e):
    if abs(e)<2:
        return 2/sqrt(4-e**2)
    else:
        return 0

Apparently Kwant uses a different convention for density of states -- which results in an extra 2 pi

In [ ]:
tdos=[theorydos(e)/(2*pi) for e in filtelist]

In [ ]:
plot(filtelist,dos)
plot(filtelist,tdos,".")

Since Kwant doesn't actually use the Greens function, it does not directly calculate it, but it gives all the info we need to calculate it.  Note, for a device with more than one site the most obvious approach is to use matrix inversion (dont forget that and energy should be multiplied by the identity matrix).  This matrix inversion is relatively expensive -- the naive algorithm scales as $n^3$, for a $n\times n$ matrix.  The best matrix inversion algorithms scale as $n^{2.373}$.  Of course one can use $LR$ decomposition calculate $\Gamma_L G \Gamma_R G^\dagger$ without ever calculating $G$ -- and due to the sparse nature of $H$, these will scale as $n$ (I think).  Alternatively you can construct $G$ from the wavefunctions that Kwant calculates.

In [ ]:
def mygreen(energy):
    return 1/(energy-h[0,0]-rightleadselfenergy(energy)[0,0]-leftleadselfenergy(energy)[0,0])

In [ ]:
mydos=[-2*imag(mygreen(e))/(2*pi) for e in filtelist]  #I put kwant's factor of 2pi here -- even though I don't like it

In [ ]:
plot(filtelist,mydos)
plot(filtelist,tdos,".")

I won't go through calculating $G$ from the wavefunctions.  I will however show how to get kwant to give us the scattering wavefunctions (which are kind of boring in this case where the device is a single site).  Nonetheless:

In [ ]:
wf=kwant.wave_function(finaldevice,-2+0.01)

In [ ]:
wf(0) # wavefunction incident from the right lead -- it is just a number, so not too interesting

Of course the thing that kwant is really designed for is calculating conductivity.  Here is one possible way to extract this.

In [ ]:
trans=[]
for energy in elist:

    # compute the scattering matrix at a given energy
    smatrix = kwant.smatrix(finaldevice, energy)

    # compute the transmission probability from left lead to
    # right lead
    trans.append(smatrix.transmission(1, 0))

In [ ]:
plot(elist,trans)
ylabel("Conductivity [q^2/h]")
xlabel("Chemical Potential [t]")

Plot the conductivity vs chemical potential when I put an on-site potential of $\epsilon_0=0.5$ on the dot. [We calculated this in one of the home-works.]

<h3> Under the Hood </h3>

If you are like me, you want to know a bit more about what the various objects are.  The documentation definitely helps.  Here are a few observations.

In [ ]:
originsite=chain_geometry(0) # this is the object which defines one of the sites (the one at x=0)

In [ ]:
originsite.pos # tells us the site's location

In [ ]:
originsite.family # tells us what lattice the site belongs to

In [ ]:
chain_geometry.closest(0.2) # finds site which is closest to x=0.2

In [ ]:
chain_geometry.n_closest(0.2,5) # finds the 5 sites closest to x=0.2

In [ ]:
neighborfunc=chain_geometry.neighbors(1)[0] # creates an object which knows how to find neighbors

In [ ]:
device2=kwant.Builder() 
device2[chain_geometry(0)]=0
device2[chain_geometry(1)]=0
device2[chain_geometry(2)]=0

In [ ]:
[i for i in neighborfunc(device2)] # prints out all sets of neighbors

<H2> Four Terminal Device </H2>

Now lets up our game -- and construct a 4-terminal device -- which will live in 2D space instead of 1D space

For the leads, we need to introduce 3 different translational symmetries

In [ ]:
rsym=kwant.TranslationalSymmetry((1,0)) # defines a translational symmetry in the x direction
lsym=kwant.TranslationalSymmetry((-1,0)) # -x direction
dsym=kwant.TranslationalSymmetry((0,-1)) # -y direction

In [ ]:
square_geometry=kwant.lattice.square(norbs=1) # defines a 2D square lattice 

In [ ]:
four_device=kwant.Builder() # container object for the device
for i in arange(10):
    four_device[square_geometry(i,0)]=0  #add site to device
for i in arange(9):
    four_device[(square_geometry(i,0),square_geometry(i+1,0))]=-1  # add hopping
four_device[square_geometry(1,-1)]=0 # add nub for lead to voltmeter
four_device[square_geometry(8,-1)]=0 # add nub for second lead to voltmeter
four_device[(square_geometry(1,0),square_geometry(1,-1))]=-0.5# add weak coupling to voltmeter lead
four_device[(square_geometry(8,0),square_geometry(8,-1))]=-0.5# add weak coupling to voltmeter lead

In [ ]:
rlead=kwant.Builder(rsym)  #create right lead
llead=kwant.Builder(lsym)  # create left lead
vlead1=kwant.Builder(dsym) # create downward pointing lead
vlead2=kwant.Builder(dsym) # create another downward pointing lead

In [ ]:
rlead[square_geometry(1,0)]=0 # Adds one site to lead
rlead[square_geometry(1,0),square_geometry(2,0)]=-1 # adds hopping to lead
llead[square_geometry(1,0)]=0 # Adds one site to lead
llead[square_geometry(1,0),square_geometry(2,0)]=-1 # adds hopping to lead

In [ ]:
vlead1[square_geometry(1,0)]=0 # Adds one site to lead
vlead1[square_geometry(1,0),square_geometry(1,1)]=-1
vlead2[square_geometry(8,0)]=0 # Adds one site to lead
vlead2[square_geometry(8,0),square_geometry(8,1)]=-1

In [ ]:
four_device.attach_lead(rlead)
four_device.attach_lead(llead)
four_device.attach_lead(vlead1)
four_device.attach_lead(vlead2)

In [ ]:
kwant.plot(four_device);

We are going to pass a voltage down this horizontal wire -- the two leads to the bottom are envisioned to go to a voltmeter.

In [ ]:
finalfour=four_device.finalized() # do all the math to calculate self-energies, find H, etc

In [ ]:
showmat(finalfour.hamiltonian_submatrix())

We can get the positions of each of these orbitals

In [ ]:
sitepos=[finalfour.pos(i) for i in range(12)]
sitepos

Here is a function which when passed the energy returns the four self-energy matrices of from the four leads

In [ ]:
def findsigmas(en):
    fourleads=finalfour.leads
    interfaces=finalfour.lead_interfaces
    sigmalist=[]
    for lead,interface in zip(fourleads,interfaces):
        sigma=zeros([12,12],complex)
        sigma[interface,interface]=lead.selfenergy(en)
        sigmalist.append(sigma)
    return sigmalist

In [ ]:
sig=findsigmas(0)
showmat(sig[0])  

In [ ]:
showmat(sig[1])

In [ ]:
showmat(sig[2])

In [ ]:
showmat(sig[3])

Construct a function which creates the Greens function for this device -- it will be a 10x10 matrix.  Verify that the diagonal elements agree with the local density of states which can be extracted from <code>kwant.ldos</code>.

Now I will show how to get the voltage drops, given a current passing through the leads

In [ ]:
trans=[]
condmats=[]
elist=arange(-3.01,3,0.1)
for energy in elist:
    
    transmatrix=zeros((4,4))
    cmatrix=zeros((4,4))

    # compute the scattering matrix at a given energy
    smatrix = kwant.smatrix(finalfour, energy)

    # compute the transmission probabilities
    for i in range(4):
        for j in range(4):
            transmatrix[i,j]=smatrix.transmission(i, j)
            cmatrix[i,j]+=transmatrix[i,j]
            cmatrix[i,i]-=transmatrix[i,j]
        
    trans.append(transmatrix)
    condmats.append(cmatrix)

The Matrices $G$ in <code>condmats</code> relate the voltages and current as
$$
\left(\begin{array}{c}I\\-I\\0\\0\end{array}\right)=
G \left(\begin{array}{c}V_R\\V_L\\V_1\\V_2\end{array}\right).
$$
The voltage drop between the current leads is $V_L-V_R$, which we will refer to as the two-terminal voltage.  The voltmeter on the other leads reads $V_2-V_1$, which is the two-terminal voltage.  Given the currents, we can readily calculate all the voltages.

I am probably a bit feeble-minded, but I always feel it is simpler to thing about applying a voltage difference, then measureing a current.  If we thing about it that way, then we write the conductivity matrix $G$ as
$$
G = \left(
\begin{array}{cc}
A&B\\C&D
\end{array}
\right)
$$
where $A,B,C,D$ are all $2\times2$ matrices.  In which case we can write
$$
 \left(
\begin{array}{cc}
\begin{array}{cc}1&0\\0&1\end{array}
&-B\\
\begin{array}{cc}0&0\\0&0\end{array}
&-D
\end{array}
\right)
\left(\begin{array}{c}I_R\\I_L\\V_1\\V_2\end{array}\right)
=
\left(\begin{array}{c}A\\C\end{array}\right)
\left(\begin{array}{c}V_R\\V_L\end{array}\right)
$$
where $I_R=-I_L=I$

In [ ]:
elist[30]

In [ ]:
showmat(trans[22])

In [ ]:
showmat(trans[22][2:,:2])

In [ ]:
showmat(condmats[22])

In [ ]:
condmats[30][1].sum()

In [ ]:
def findiv(condmat):
    A=condmat[:2,:2]
    B=condmat[2:,:2]
    C=condmat[:2,2:]
    D=condmat[2:,2:]
    LHS=block([[eye(2).toarray(),-B],[zeros((2,2)),-D]])
    RHS=concatenate((A.dot(array((1,0))),C.dot(array((1,0)))))
    try:
        (il,ir,v1,v2)=linalg.solve(LHS,RHS)
    except: # linear system is ill-behaved -- typically because conductivity vanishes =
        v2=1
        v1=0
        ir=0
    result={"I":ir,"V":1,"Vvoltmeter":v2-v1}
    return result

In [ ]:
findiv(condmats[22])

In [ ]:
twoterminalResistivity=[]
fourterminalResistivity=[]
for condmat in condmats:
    vlist=findiv(condmat)
    twoterminalResistivity.append(vlist["V"]/(vlist["I"]+1e-6))
    fourterminalResistivity.append(vlist["Vvoltmeter"]/(vlist["I"]+1e-6))

The following graph shows the two-terminal resistivity in Blue, and the four terminal resistivity in orange.  Without the voltage leads, the two-terminal resistance should be 1 (the Landauer result), but we have back-scattering off the leads.  We see spikes in the 4-terminal resistance, corresponding to resonances.

In [ ]:
plot(elist,twoterminalResistivity)
plot(elist,fourterminalResistivity)
xlabel("$\mu$")
ylabel("$V/I$")
ylim(0,2)

We get further insight by looking at the density of states

Lets begin by finding the chemical potentials corresponding to the maxima and the minima

In [ ]:
slopesign=sign(array(fourterminalResistivity)[1:]-array(fourterminalResistivity)[:-1])
slopesigndif=slopesign[1:]-slopesign[:-1]
mins=where(slopesigndif==2)[0]+2
maxs=where(slopesigndif==-2)[0]+2

In [ ]:
mins

In [ ]:
elist[mins]

In [ ]:
elist[maxs]

In [ ]:
mydos1=kwant.ldos(finalfour,elist[mins[1]])
mydos2=kwant.ldos(finalfour,elist[maxs[1]])
mydos1

In [ ]:
kwant.plot(finalfour,site_size=3*mydos1, site_color=(0, 0, 1, 0.3)); # wavefuntion has nodes at leads

In [ ]:
kwant.plot(finalfour,site_size=3*mydos2, site_color=(0, 0, 1, 0.3));

Another way to plot things is to just extract the 1D array of sites where y=0

In [ ]:
mainbranch=[j==0 for (i,j) in sitepos]
mainbranch

We then calculate the density of states on each of these sites

In [ ]:
dosdat=[]
for e in elist:
    dosdat.append(kwant.ldos(finalfour,e)[mainbranch])

In [ ]:
dosdat[30]

In [ ]:
imshow(dosdat,extent=(0,10,elist[0],elist[-1]),vmax=0.26,vmin=0.)
colorbar()
ylabel("$\mu$")
xlabel("site")
for j in mins[:-1]:
    plot((0,10),(elist[j],elist[j]),"black")
for j in maxs[:-1]:
    plot((0,10),(elist[j],elist[j]),"red")

In [ ]:
for j,dos in enumerate(transpose(array(dosdat))):
       plot(elist,dos+0.1*j,".")
ylim(0,1.5)
for j in mins[:-1]:
    plot((elist[j],elist[j]),(0,1.5),"black")
for j in maxs[:-1]:
    plot((elist[j],elist[j]),(0,1.5),"red")

Make the coupling to the leads weaker by changing the hopping to the nubs from -0.5 to -0.1.  How does this change the results?  How about also dropping the strength of the coupling between the first two and last two sites to -0.1 (so that all leads are only weakly coupled)?

<h2> Quantum Hall Effect </h2>

Lets now do a real 2D system, and investigate the quantum Hall effect

In [ ]:
hallbar=kwant.Builder()

In [ ]:
length=30
width=20
leftleadwidth=10
rightleadwidth=10
leftleadspace=5
rightleadspace=5
sideleadwidth=10
sideleadspace=5
fluxperplaquette=0.1

In [ ]:
for i in range(length):
    for j in range(width):
        hallbar[square_geometry(i,j)]=0

In [ ]:
for i in range(length-1):
    for j in range(width):
        hallbar[(square_geometry(i,j),square_geometry(i+1,j))]=-1

In [ ]:
vert=[]
for i in range(length):
    for j in range(width-1):
        vert.append((i,j))
        hallbar[(square_geometry(i,j),square_geometry(i,j+1))]=-exp(2*pi*1j*i*fluxperplaquette)

In [ ]:
kwant.plot(hallbar);

In [ ]:
rsym=kwant.TranslationalSymmetry((1,0)) # defines a translational symmetry in the x direction
lsym=kwant.TranslationalSymmetry((-1,0)) # -x direction
dsym=kwant.TranslationalSymmetry((0,-1)) # -y direction
usym=kwant.TranslationalSymmetry((0,1)) # y direction

In [ ]:
rlead=kwant.Builder(rsym)  #create right lead
ulead1=kwant.Builder(usym)
ulead2=kwant.Builder(usym)
llead=kwant.Builder(lsym)  # create left lead
dlead2=kwant.Builder(dsym)
dlead1=kwant.Builder(dsym) # create downward pointing lead

In [ ]:
for j in arange(rightleadspace,rightleadspace+rightleadwidth):
    rlead[square_geometry(length,j)]=0
    rlead[(square_geometry(length,j),square_geometry(length+1,j))]=-exp(-2*pi*1j*j*fluxperplaquette)
for j in arange(rightleadspace,rightleadspace+rightleadwidth-1):
    rlead[(square_geometry(length-1,j),square_geometry(length-1,j+1))]=-exp(2*pi*1j*(length-1)*fluxperplaquette)

In [ ]:
for j in arange(leftleadspace,leftleadspace+leftleadwidth):
    llead[square_geometry(0,j)]=0
    llead[(square_geometry(0,j),square_geometry(1,j))]=-exp(-2*pi*1j*j*fluxperplaquette)
for j in arange(leftleadspace,leftleadspace+leftleadwidth-1):
    llead[(square_geometry(0,j),square_geometry(0,j+1))]=-1

In [ ]:
for i in arange(sideleadspace,sideleadspace+sideleadwidth):
    dlead1[square_geometry(i,0)]=0
    dlead2[square_geometry(length-i,0)]=0
    ulead1[square_geometry(i,0)]=0
    ulead2[square_geometry(length-i,0)]=0
    dlead1[(square_geometry(i,0),square_geometry(i,1))]=-exp(2*pi*1j*i*fluxperplaquette)
    dlead2[(square_geometry(length-i,0),square_geometry(length-i,1))]=-exp(2*pi*1j*(length-i)*fluxperplaquette)
    ulead1[(square_geometry(i,width),square_geometry(i,width+1))]=-exp(2*pi*1j*i*fluxperplaquette)
    ulead2[(square_geometry(length-i,width),square_geometry(length-i,width+1))]=-exp(2*pi*1j*(length-i)*fluxperplaquette)
for i in arange(sideleadspace,sideleadspace+sideleadwidth-1):
    dlead1[(square_geometry(i,0),square_geometry(i+1,0))]=-1
    dlead2[(square_geometry(length-i,0),square_geometry(length-i-1,0))]=-1
    ulead1[(square_geometry(i,0),square_geometry(i+1,0))]=-1
    ulead2[(square_geometry(length-i,0),square_geometry(length-i-1,0))]=-1

In [ ]:
hallbar.attach_lead(llead)
hallbar.attach_lead(dlead1)
hallbar.attach_lead(dlead2)
hallbar.attach_lead(rlead)
hallbar.attach_lead(ulead2)
hallbar.attach_lead(ulead1)

In [ ]:
kwant.plot(hallbar);

In [ ]:
hallfinal=hallbar.finalized()

Lets now look at the properties of the leads

In [ ]:
hallleads=hallfinal.leads

We can see which sites they are attached to

In [ ]:
hallfinal.lead_interfaces

We can look at their Hamiltonians

In [ ]:
showmat(hallleads[0].cell_hamiltonian())

In [ ]:
showmat(hallleads[0].inter_cell_hopping())

The dispersion for the lead can be found from

In [ ]:
def leaddisp(k):
    H= hallleads[0].cell_hamiltonian()
    lam=hallleads[0].inter_cell_hopping()
    clam=lam.transpose().conjugate()
    ham=H+exp(-1j*(k+pi*fluxperplaquette))*lam+ exp(1j*(k+pi*fluxperplaquette))*clam
    evals=linalg.eigvalsh(ham)
    return evals

In [ ]:
leadens=array([leaddisp(k) for k in arange(-pi,pi+pi/50,pi/50)])

In [ ]:
klist=arange(-pi,pi+pi/50,pi/50)

In [ ]:
for ens in leadens.transpose():
    plot(klist,ens)

At low energies, and small $k$, one sees Landau levels (the flat regions).  These bend up at large k -- making edge modes.  At $E$ near 0 there is extra structure, which is related to Hofstaedter's butterfly.  At high energies one again sees Landau levels, but they are centered around $k=\pi$.  They correspond to holes instead of particles.

Of course, kwant has a built-in function for doing exactly what we just did. (though it is not smart enough to know how to center the dispersion when there is a magnetic field.  [The zero of k is somewhat arbitrary -- you can always shift it with a Gauge transformation.]

In [ ]:
kwant.plotter.bands(hallleads[0]);

Next calculate the conductivity matrix

In [ ]:
htrans=[]
hcondmats=[]
helist=arange(-4.01,4,0.05)
for energy in helist:
    
    transmatrix=zeros((6,6))
    cmatrix=zeros((6,6))

    # compute the scattering matrix at a given energy
    smatrix = kwant.smatrix(hallfinal, energy)

    # compute the transmission probabilities
    for i in range(6):
        for j in range(6):
            transmatrix[i,j]=smatrix.transmission(i, j)
            cmatrix[i,j]+=transmatrix[i,j]
            cmatrix[i,i]-=transmatrix[i,j]
        
    htrans.append(transmatrix)
    hcondmats.append(cmatrix)

interestngly-- at some energies, the transmission matrix is a permutation matrix -- all the incoming states from one lead end up at the next lead over -- this is due to edge states

In [ ]:
helist[21]

In [ ]:
showmat(htrans[21]) 

In [ ]:
showmat(htrans[45]) 

We can summarize this behavior by looking at the transmission elements between the far left lead, and its two neighbors

In [ ]:
plot(helist,[trans[0,1] for trans in htrans])
plot(helist,[trans[0,5] for trans in htrans])

Of course, if we tune the energy just right we can get some backscattering

In [ ]:
sboundary = kwant.smatrix(hallfinal, -2.352)

In [ ]:
transmatrixb=array([[sboundary.transmission(i,j) for i in range(6)] for j in range(6)])
showmat(transmatrixb)

This sort of device is typically current biased, and the voltages are measured on the four side-leads

In [ ]:
def hfindiv(condmat):
    i=(1,0,0,-1,0,0)
    try:
        vs=linalg.solve(condmat,(1,0,0,-1,0,0))
        err=0 # used for diagnostics
    except: # can't solve linear system -- set one voltage to zero
        try:
            shortvs=linalg.solve(condmat[:-1,:-1],(1,0,0,-1,0))
            vs=append(shortvs,0)
            err=1
        except: # if that doesn't work, probably means current is zero
            i=(0,0,0,0,0,0)
            vs=(0,0,0,0,0,0)
            err=2
    result={"I":i,"V":vs,"err":err}
    return result

We can then use these voltages and currents to tabulate the resistivity

In [ ]:
longresist=[]
hallresist=[]
errlist=[]
for condmat in hcondmats:
    iv=hfindiv(condmat)
    i=iv["I"]
    v=iv["V"]
    errlist.append(iv["err"])
    current=i[0]-i[3]
    longvolt=v[2]-v[1]
    perpvolt=v[5]-v[1]
    longresist.append(longvolt/(current+1e-6))
    hallresist.append(-perpvolt/(current+1e-6))

In [ ]:
plot(helist,hallresist)
plot(helist,longresist)

Make a new energy grid which lets you zoom in between E=-2 and E=-2.5.  You should see more structure in the longitudinal and hall resistivity.

Add microscopic disorder to this problem -- by adding random on-site potentials.  Play a bit with the magnitudes. You should be able to get a regime where the quantized hall conductance plateaus exist, but there are "normal" regions between them.

<h3> Internal Currents </h3>

Given the way that kwant stores the information about the system, we can extract the currents by finding all the incoming wave-functions, weighting them by the voltage of that lead, then calculating the contribution to the current from that wavefunction.

In [ ]:
qhwf=kwant.wave_function(hallfinal,-2)

If we iterate over the leads we can see how many incoming channels there are at each lead

In [ ]:
for i in range(6):
    print(len(qhwf(i)))

We can plot the absolute magnitude squared of the various wavefunctions

In [ ]:
kwant.plotter.map(hallfinal,abs(qhwf(0)[0])**2);

In [ ]:
kwant.plotter.map(hallfinal,abs(qhwf(1)[0])**2);

In [ ]:
kwant.plotter.map(hallfinal,abs(qhwf(2)[0])**2);

Now we can calculate the contribution to the current from any given wavefunction

In [ ]:
currentop=kwant.operator.Current(hallfinal)

This can be plotted

In [ ]:
kwant.plotter.current(hallfinal,currentop(qhwf(2)[0]));

Now lets add up all the contributions

In [ ]:
currents=[]
voltages=[1,-1,-1,-1,1,1]
for i in range(6):
    wfs=qhwf(i)
    for wf in wfs:
        currents.append(voltages[i]*currentop(wf));

In [ ]:
totalcurrent= array(currents).sum(0)

In [ ]:
kwant.plotter.current(hallfinal,totalcurrent);

Try energy -2.352.  Try your disordered system.